---
# Boundary velocity smart speaker in a room
---

In this demo we will showcase how a smart speaker with both source and receivers can be placed in a room scenario and simulated in the SDK.

Let's initialize the SDK and create a project:

In [ ]:
import numpy as np
from treble_tsdk import treble

tsdk = treble.TSDK()

project = tsdk.get_or_create_project(
    name="bv_smartspeaker", description="Loudspeaker with source and receivers on it"
)

Display room model database

In [ ]:
dd.display(tsdk.geometry_library.list_datasets_with_count())

Retrieve a room from the geometry database:

In [ ]:
meeting_rooms = tsdk.geometry_library.get_dataset("MeetingRoom")
room = meeting_rooms[18]
room.plot()

Assign materials to the room layers:

In [ ]:
materials = {
    "Chairs": tsdk.material_library.get_by_name("Upholstered seating, well upholstered"),
    "Light wall": tsdk.material_library.get_by_name("Gypsum/Plaster on solid backing"),
    "Concrete wall": tsdk.material_library.get_by_name("Concrete block, painted"),
    "Floor": tsdk.material_library.get_by_name("Wooden flooring"),
    "Table": tsdk.material_library.get_by_name("Wood"),
    "Acoustic": tsdk.material_library.get_by_name("Glasswool 20 mm, 25 kg/m3"),
    "Door": tsdk.material_library.get_by_name("Wooden door"),
    "Window": tsdk.material_library.get_by_name("Double 2-3 mm glass, >30 mm air gap"),
    "Ceiling": tsdk.material_library.get_by_name("Acoustic plaster"),
    "Monitor": tsdk.material_library.get_by_name("Single pane of glass, >4 mm"),
}
material_assignment = []
for layer in room.layer_names:
    material = materials[layer]
    material_assignment.append(treble.MaterialAssignment(layer, material))

In this example, a loudspeaker boundary velosity source is created by following these steps:
- The loudspeaker geometry is created with the function `create_loudspeaker`. It is also possible to import a geometry from a local file.
- The free-field model is created.
- The free-field simulation is created and run. 
- The submodel is made, which is later used in the simulations.

Let's create the loudspeaker geometry:

In [131]:
speaker_width = 0.12
speaker_depth = 0.1
speaker_height = 0.5
membrane_diemeter = 0.05
speaker = treble.GeometryComponentGenerator.create_loudspeaker(
    width=speaker_width,
    depth=speaker_depth,
    height=speaker_height,
    membrane_diameter=membrane_diemeter,
    membrane_center_height=0.25,
)

Now the free-field model of the loudspeaker:

In [ ]:
# Create the freefield model
ff_model_name = "MeetingRoomBarModel"
ff_model = project.get_model_by_name(ff_model_name)
if not ff_model:
    ff_model = treble.free_field.add_free_field_model(
        project=project, name=ff_model_name, geometry=speaker, sphere_geometry_radius=2
    )
ff_model.plot()

Let's run the freefield simulation of the loudspeaker:

In [ ]:
loudspeaker_name = "MeetingRoomBar"
ff_sim = project.get_simulation_by_name(loudspeaker_name)
if not ff_sim:
    ff_settings = treble.free_field.FreeFieldSimulationSettings()
    sim_def = treble.free_field.FreeFieldSimulationDefinition(
        name=loudspeaker_name,
        frequency=8000,
        free_field_model=ff_model,
        receiver_sphere_radius=1.0,
        source_input="membrane",
        free_field_simulation_settings=ff_settings,
    )
    sim_def.validate().as_tree()
    ff_sim = project.add_simulation(sim_def)
    ff_sim.wait_for_estimate().as_tree()
    ff_sim.start()
    ff_sim.as_live_progress()
ff_sim.plot()

Lastly, create the loudspeaker boundary velocity submodel:

In [ ]:
sub_source_name = "Bar for meeting room"
sub_source = tsdk.boundary_velocity_submodel_library.get_by_name(sub_source_name)
if not sub_source:
    print("source submodel not found, creating a new one")
    ff_results = ff_sim.get_results_object(f"/tmp/{ff_sim.id}")
    sub_source = ff_results.create_boundary_velocity_submodel(
        source_name=sub_source_name, source_description=""
    )

Define source locations:

In [ ]:
# Omni-source locations
omnis = [
    x for x in room.position_suggestions if x.name in ["monitor_right", "table_edge_s"]
]

# Speech-source locations
speeches = [
    x
    for x in room.position_suggestions
    if x.name in ["chair_0", "chair_1", "monitor_left"]
]

# Loudspeaker position
table_center = [x for x in room.position_suggestions if x.name == "table_center"][0]

Generate a list of sources for inclusion in the simulation definition:

In [ ]:
def point_towards(from_loc: treble.Point3d, to_loc: treble.Point3d) -> treble.Rotation:
    azimuth = np.arctan2(to_loc.y - from_loc.y, to_loc.x-from_loc.x) * 180 / np.pi
    return treble.Rotation(azimuth=azimuth)

source_list = []

# omnis
for omni in omnis:
    source_list.append(treble.Source.make_omni(position=omni.position, label=omni.name))

# speeches
for speech in speeches:
    source_list.append(
        treble.Source.make_directive(
            position=speech.position,
            label=speech.name,
            source_directivity=tsdk.source_directivity_library.get_by_name("Speech"),
            orientation=point_towards(
                from_loc=speech.position, to_loc=table_center.position
            ),
        )
    )

Create the boundary velocity submodel source and add it to the list of sources:

In [ ]:
bv_location = table_center.position - treble.Point3d(0, 0, 0.2)
bv_source = treble.Source.make_boundary_velocity_submodel(
    position=bv_location,
    orientation=treble.Rotation(elevation=90),
    label=loudspeaker_name,
    boundary_velocity_submodel=sub_source,
)
source_list.append(bv_source)

Define receiver locations:

In [ ]:
receiver_offsets = [
    treble.Point3d(0.1, 0, 0.01),
    treble.Point3d(-0.1, 0, 0.01),
    treble.Point3d(0, speaker_width / 2 - 0.02, 0.01),
    treble.Point3d(0, -(speaker_width / 2 - 0.02), 0.01),
]
receiver_list = [treble.Receiver.make_mono(position=bv_location + receiver_offsets[_i], label=f"Receiver_{_i}") for _i in range(len(receiver_offsets))]

Create the Simulation Definition:

In [ ]:
# Define the inputs to the simulation, i.e. the type, model, frequency, IR length, source and receiver list, materials and GA settings
simulation_name = "room_soundbar_demo_500Hz"
simulation_definition = treble.SimulationDefinition(
    name=simulation_name,
    simulation_type=treble.SimulationType.dg,
    model=room,
    crossover_frequency=8000,
    energy_decay_threshold=30,
    receiver_list=receiver_list,
    source_list=source_list,
    material_assignment=material_assignment,
    simulation_settings=treble.SimulationSettings(),
)

# Validate and plot simulation definition
validation_results = simulation_definition.validate()
treble.dd.display(validation_results)
simulation_definition.plot()

Let's run simulation and monitor the progress:

In [ ]:
simulation = project.get_simulation_by_name(simulation_name)
if not simulation:
    simulation = project.add_simulation(simulation_definition)
    simulation.wait_for_estimate()
    simulation.start()
simulation.as_live_progress()

You can download simulation results by calling the `get_results_object` method. This download package includes IRs as well as result parameters as `JSON` files.

In [ ]:
simulation = project.get_simulation_by_name(simulation_name)
if simulation.status == "Completed":
    sim_results = simulation.get_results_object(f"/tmp/{simulation.id}")

Let's visualize the results:

In [ ]:
sim_results.plot()